In [1]:
# import pytorch libraries
%matplotlib inline
from collections import Counter
import numpy as np
import pickle
import pandas as pd
import torch 
import torch.autograd as autograd 
import torch.nn as nn 
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader, Dataset
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import Lasso
from sklearn.linear_model import Ridge
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import Lasso
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import cross_val_score
import xgboost as xgb
import spacy
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import CountVectorizer
import nltk


In [2]:
pickle_file_path = 'data/train.pickle'

In [3]:
with open(pickle_file_path, 'rb') as file:
    # Load the data from the file
    training_data = pickle.load(file)
training_data = pd.DataFrame(training_data)
training_data.head(5)

price                                              title  \
0  320.000 €  Piso Tallers. Piso con 2 habitaciones con asce...   
1  335.000 €  Piso C/ de valència. Piso reformado en venta d...   
2  330.000 €  Piso en Dreta de l´Eixample. Acogedor piso al ...   
3  435.000 €  Piso Barcelona - corts catalanes. Soleado, cén...   
4  410.000 €  Piso en Carrer de sardenya 271. Alto, reformad...   

                        loc_string                     loc  \
0          Barcelona - Sant Antoni                    None   
1  Barcelona - Dreta de l´Eixample                    None   
2  Barcelona - Dreta de l´Eixample                    None   
3          Barcelona - Sant Antoni                    None   
4      Barcelona - Sagrada Família  Carrer de Sardenya 271   

                               features  type subtype     selltype  \
0   [85 m2, 2 hab., 1 baño, 3.647 €/m2]  FLAT    FLAT  SECOND_HAND   
1   [65 m2, 2 hab., 1 baño, 5.000 €/m2]  FLAT    FLAT  SECOND_HAND   
2   [77 m2, 2 hab., 1 baño, 4.286 €/m2]  FLAT    FLAT  SECOND_HAND   
3  [96 m2, 3 hab., 2 baños, 4.531 €/m2]  FLAT    FLAT  SECOND_HAND   
4   [84 m2, 2 hab., 1 baño, 4.881 €/m2]  FLAT    FLAT  SECOND_HAND   

                                                desc  
0  Piso en última planta a reformar en calle Tall...  
1  Ubicado en la zona del Camp de l’Arpa, cerca d...  
2  En pleno centro de Barcelona, justo al lado de...  
3  Vivienda espaciosa en Sant Antoni, cerca de Pl...  
4  En el corazón de Barcelona, en una hermosa fin...

In [4]:
test_pickle_file_path = 'data/test_kaggle.pickle'

with open(test_pickle_file_path, 'rb') as file:
    test_data = pickle.load(file)
test_data = pd.DataFrame(test_data)
# test_data['price'] = "0.00 €"
test_data.insert(0, 'price', "0.00 €")
test_data = test_data.drop(columns=['id', 'description'])
test_data.head(5)

price                                              title  \
0  0.00 €  Piso Carrer de llull. Piso con 4 habitaciones ...   
1  0.00 €  Piso Diagonal. Luminoso piso de 4 habitaciones...   
2  0.00 €  Piso Carrer del consell de cent. Piso amueblad...   
3  0.00 €                     Piso Castanys. Carrer castanys   
4  0.00 €  Piso Carrer de casanova. Piso con 2 habitacion...   

                                      loc_string   loc  \
0  Barcelona - El Parc i la Llacuna del Poblenou  None   
1                           Barcelona - Poblenou  None   
2    Barcelona - L´Antiga Esquerra de l´Eixample  None   
3                           Barcelona - Poblenou  None   
4                        Barcelona - Sant Antoni  None   

                  features  type subtype     selltype  \
0  [87 m2, 4 hab., 1 baño]  FLAT    FLAT  SECOND_HAND   
1  [78 m2, 4 hab., 1 baño]  FLAT    FLAT  SECOND_HAND   
2  [65 m2, 1 hab., 1 baño]  FLAT    FLAT  SECOND_HAND   
3  [88 m2, 3 hab., 1 baño]  FLAT    FLAT  SECOND_HAND   
4  [82 m2, 2 hab., 1 baño]  FLAT    FLAT  SECOND_HAND   

                                                desc  
0  Contactar con Camila 7. 3.\n\nLa Casa Agency E...  
1  ¡Un gran piso a reformar es una gran oportunid...  
2  AUREA INMOBILIARIA PRESENTA, ACOGEDOR APARTAME...  
3  Piso en pleno centro de Poblenou, techos altos...  
4  Punt Zona Franca presenta esta fantástica vivi...

In [5]:
training_data = pd.concat([training_data, test_data], ignore_index=True)

In [6]:
training_data['type'].unique()

array(['FLAT', 'STUDIO', 'GROUND_FLOOR', 'PENTHOUSE', 'APARTMENT', 'LOFT',
       'DUPLEX'], dtype=object)

In [7]:
training_data['selltype'].unique()

array(['SECOND_HAND'], dtype=object)

In [8]:
dummies = pd.get_dummies(training_data['type'])
training_data
training_data_with_dummies = pd.concat([training_data, dummies], axis=1)
training_data_with_dummies.drop('type', axis=1, inplace=True)

In [9]:
row = training_data_with_dummies['features'][0]

In [10]:
print(row)

['85 m2', '2 hab.', '1 baño', '3.647 €/m2']


In [11]:
training_data.head(5)

price                                              title  \
0  320.000 €  Piso Tallers. Piso con 2 habitaciones con asce...   
1  335.000 €  Piso C/ de valència. Piso reformado en venta d...   
2  330.000 €  Piso en Dreta de l´Eixample. Acogedor piso al ...   
3  435.000 €  Piso Barcelona - corts catalanes. Soleado, cén...   
4  410.000 €  Piso en Carrer de sardenya 271. Alto, reformad...   

                        loc_string                     loc  \
0          Barcelona - Sant Antoni                    None   
1  Barcelona - Dreta de l´Eixample                    None   
2  Barcelona - Dreta de l´Eixample                    None   
3          Barcelona - Sant Antoni                    None   
4      Barcelona - Sagrada Família  Carrer de Sardenya 271   

                               features  type subtype     selltype  \
0   [85 m2, 2 hab., 1 baño, 3.647 €/m2]  FLAT    FLAT  SECOND_HAND   
1   [65 m2, 2 hab., 1 baño, 5.000 €/m2]  FLAT    FLAT  SECOND_HAND   
2   [77 m2, 2 hab., 1 baño, 4.286 €/m2]  FLAT    FLAT  SECOND_HAND   
3  [96 m2, 3 hab., 2 baños, 4.531 €/m2]  FLAT    FLAT  SECOND_HAND   
4   [84 m2, 2 hab., 1 baño, 4.881 €/m2]  FLAT    FLAT  SECOND_HAND   

                                                desc  
0  Piso en última planta a reformar en calle Tall...  
1  Ubicado en la zona del Camp de l’Arpa, cerca d...  
2  En pleno centro de Barcelona, justo al lado de...  
3  Vivienda espaciosa en Sant Antoni, cerca de Pl...  
4  En el corazón de Barcelona, en una hermosa fin...

In [12]:

def clean_features(lst):
    # Initialize all variables with NaN to handle missing values
    square_m = hab = bano = np.nan
    
    # Process each element in the list if it exists
    if len(lst) > 0 and lst[0]:
        square_m, _ = lst[0].split(' ')
        square_m = float(square_m)
    
    if len(lst) > 1 and lst[1]:
        hab, _ = lst[1].split(' ')
        hab = float(hab)
    
    if len(lst) > 2 and lst[2]:
        # Check if 'bano' information is available or it's the price per square meter
        if 'baño' in lst[2]:
            bano, _ = lst[2].split(' ')
            bano = float(bano)
        # else:
        #     # If 'baño' is not in the string, it might be the price info in the 'bano' slot
        #     price_per_s_m, _ = lst[2].split(' ')
        #     price_per_s_m = float(price_per_s_m)

    # if len(lst) > 3 and lst[3]:
    #     price_per_s_m, _ = lst[3].split(' ')
    #     price_per_s_m = float(price_per_s_m)
    
    return square_m, hab, bano


In [13]:
def fix_euros(element):
    price, _ = element.split(' ')
    return float(price)

In [14]:
square_m, hab, bano = clean_features(row)

In [15]:
square_m_list , hab_list, bano_list, price_list= [], [], [], []
for index, row in enumerate(training_data_with_dummies['features']):
    square_m , hab, bano =clean_features(row)
    square_m_list.append(square_m)
    hab_list.append(hab)
    bano_list.append(bano)
    # price_per_s_m_list.append(price_per_s_m)
for row in training_data_with_dummies['price']:
    price = fix_euros(row)
    price_list.append(price)

In [16]:
training_data_with_dummies['price'] = price_list
training_data_with_dummies['square_m'] = square_m_list
training_data_with_dummies['hab'] = hab_list
training_data_with_dummies['bano'] = bano_list
# training_data_with_dummies['price_per_sm'] = price_per_s_m_list
training_data_with_dummies.drop('features', axis=1, inplace=True)
training_data_with_dummies.drop('selltype', axis=1, inplace=True)

training_data_with_dummies.head()

price                                              title  \
0  320.0  Piso Tallers. Piso con 2 habitaciones con asce...   
1  335.0  Piso C/ de valència. Piso reformado en venta d...   
2  330.0  Piso en Dreta de l´Eixample. Acogedor piso al ...   
3  435.0  Piso Barcelona - corts catalanes. Soleado, cén...   
4  410.0  Piso en Carrer de sardenya 271. Alto, reformad...   

                        loc_string                     loc subtype  \
0          Barcelona - Sant Antoni                    None    FLAT   
1  Barcelona - Dreta de l´Eixample                    None    FLAT   
2  Barcelona - Dreta de l´Eixample                    None    FLAT   
3          Barcelona - Sant Antoni                    None    FLAT   
4      Barcelona - Sagrada Família  Carrer de Sardenya 271    FLAT   

                                                desc  APARTMENT  DUPLEX  FLAT  \
0  Piso en última planta a reformar en calle Tall...          0       0     1   
1  Ubicado en la zona del Camp de l’Arpa, cerca d...          0       0     1   
2  En pleno centro de Barcelona, justo al lado de...          0       0     1   
3  Vivienda espaciosa en Sant Antoni, cerca de Pl...          0       0     1   
4  En el corazón de Barcelona, en una hermosa fin...          0       0     1   

   GROUND_FLOOR  LOFT  PENTHOUSE  STUDIO  square_m  hab  bano  
0             0     0          0       0      85.0  2.0   1.0  
1             0     0          0       0      65.0  2.0   1.0  
2             0     0          0       0      77.0  2.0   1.0  
3             0     0          0       0      96.0  3.0   2.0  
4             0     0          0       0      84.0  2.0   1.0

In [17]:
# def citys_neighbhoods(text):
#     sliced = text.split(' - ') 
#     city = [sliced[0]]
#     neighborhoods = sliced[1]
#     return city, neighborhoods

In [18]:
df = pd.DataFrame()

In [19]:
# city_list, neighborhoods_list = [], []
# for i , row in enumerate(training_data_with_dummies['loc_string']):
#     city, neighborhoods, = citys_neighbhoods(row)
#     city_list.append(city)
#     neighborhoods_list.append(neighborhoods)
# df['city'] = pd.DataFrame(city_list)
# df['neighborhood'] = neighborhoods_list


In [20]:
# df['City_encoded'] = df['city'].astype('category').cat.codes
# df['Neighborhood_encoded'] = df['neighborhood'].astype('category').cat.codes
# training_data_with_dummies['City_encoded'] = df['City_encoded'] 
# training_data_with_dummies['Neighborhood_encoded'] = df['Neighborhood_encoded']
# train_set = pd.get_dummies(training_data_with_dummies, columns=['City_encoded', 'Neighborhood_encoded'])
# train_set.head(5)

In [21]:
# train_set.drop('loc_string', axis=1, inplace=True)
# train_set.drop('title', axis=1, inplace=True)
# train_set.drop('loc', axis=1, inplace=True)
# train_set.drop('desc', axis=1, inplace=True)
# train_set.drop('subtype', axis=1, inplace=True)
train_set = training_data_with_dummies
train_set.shape

(998, 16)

In [22]:
train_set.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 998 entries, 0 to 997
Data columns (total 16 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         998 non-null    float64
 1   title         998 non-null    object 
 2   loc_string    998 non-null    object 
 3   loc           103 non-null    object 
 4   subtype       998 non-null    object 
 5   desc          998 non-null    object 
 6   APARTMENT     998 non-null    uint8  
 7   DUPLEX        998 non-null    uint8  
 8   FLAT          998 non-null    uint8  
 9   GROUND_FLOOR  998 non-null    uint8  
 10  LOFT          998 non-null    uint8  
 11  PENTHOUSE     998 non-null    uint8  
 12  STUDIO        998 non-null    uint8  
 13  square_m      998 non-null    float64
 14  hab           998 non-null    float64
 15  bano          988 non-null    float64
dtypes: float64(4), object(5), uint8(7)
memory usage: 77.1+ KB


In [23]:
df = train_set
train_set.shape

(998, 16)

In [24]:
train_set.columns

Index(['price', 'title', 'loc_string', 'loc', 'subtype', 'desc', 'APARTMENT',
       'DUPLEX', 'FLAT', 'GROUND_FLOOR', 'LOFT', 'PENTHOUSE', 'STUDIO',
       'square_m', 'hab', 'bano'],
      dtype='object')

In [25]:
train_set['bano'].unique()

array([ 1.,  2., nan,  3.,  4.])

In [26]:
columns_with_nan = df.columns[df.isna().any()].tolist()
print(columns_with_nan)

['loc', 'bano']


In [27]:
df = df.drop(columns=['loc'])

In [28]:
nan_count_banos = df['bano'].isna().sum()
print(f'Number of NaN values in "banos": {nan_count_banos}')
df['bano'] = df['bano'].fillna(0)

Number of NaN values in "banos": 10


In [29]:
df.shape

(998, 15)

In [30]:
df = df.dropna()

In [31]:
df.shape

(998, 15)

In [32]:
df['subtype'].isna().sum()

0

In [33]:
df.head(5)

price                                              title  \
0  320.0  Piso Tallers. Piso con 2 habitaciones con asce...   
1  335.0  Piso C/ de valència. Piso reformado en venta d...   
2  330.0  Piso en Dreta de l´Eixample. Acogedor piso al ...   
3  435.0  Piso Barcelona - corts catalanes. Soleado, cén...   
4  410.0  Piso en Carrer de sardenya 271. Alto, reformad...   

                        loc_string subtype  \
0          Barcelona - Sant Antoni    FLAT   
1  Barcelona - Dreta de l´Eixample    FLAT   
2  Barcelona - Dreta de l´Eixample    FLAT   
3          Barcelona - Sant Antoni    FLAT   
4      Barcelona - Sagrada Família    FLAT   

                                                desc  APARTMENT  DUPLEX  FLAT  \
0  Piso en última planta a reformar en calle Tall...          0       0     1   
1  Ubicado en la zona del Camp de l’Arpa, cerca d...          0       0     1   
2  En pleno centro de Barcelona, justo al lado de...          0       0     1   
3  Vivienda espaciosa en Sant Antoni, cerca de Pl...          0       0     1   
4  En el corazón de Barcelona, en una hermosa fin...          0       0     1   

   GROUND_FLOOR  LOFT  PENTHOUSE  STUDIO  square_m  hab  bano  
0             0     0          0       0      85.0  2.0   1.0  
1             0     0          0       0      65.0  2.0   1.0  
2             0     0          0       0      77.0  2.0   1.0  
3             0     0          0       0      96.0  3.0   2.0  
4             0     0          0       0      84.0  2.0   1.0

In [34]:
df['subtype'].unique()

array(['FLAT', 'STUDIO', 'GROUND_FLOOR', 'PENTHOUSE', 'APARTMENT', 'LOFT',
       'DUPLEX'], dtype=object)

In [35]:
df['loc_string'].unique()

array(['Barcelona - Sant Antoni', 'Barcelona - Dreta de l´Eixample',
       'Barcelona - Sagrada Família', 'Barcelona - Fort Pienc',
       'Barcelona - L´Antiga Esquerra de l´Eixample',
       'Barcelona - La Nova Esquerra de l´Eixample',
       'Barcelona - La Nova Esquerra de l´Eixample\nVer mapa',
       'Barcelona - Dreta de l´Eixample\nVer mapa',
       'Barcelona - Poblenou',
       'Barcelona - El Parc i la Llacuna del Poblenou',
       'Barcelona - La Vila Olímpica del Poblenou',
       'Barcelona - Poblenou\nVer mapa',
       'Barcelona - El Camp de l´Arpa del Clot',
       'Barcelona - Besòs - Maresme',
       'Barcelona - Diagonal Mar i el Front Marítim del Poblenou',
       'Barcelona - Provençals del Poblenou', 'Barcelona - El Clot',
       'Barcelona - Navas', 'Barcelona - Sagrada Família\nVer mapa'],
      dtype=object)

## Continuing encoding subtype and loc_string

In [36]:
df = pd.get_dummies(df, columns=['subtype', 'loc_string'])

In [37]:
df2 = df
df2

price                                              title  \
0    320.0  Piso Tallers. Piso con 2 habitaciones con asce...   
1    335.0  Piso C/ de valència. Piso reformado en venta d...   
2    330.0  Piso en Dreta de l´Eixample. Acogedor piso al ...   
3    435.0  Piso Barcelona - corts catalanes. Soleado, cén...   
4    410.0  Piso en Carrer de sardenya 271. Alto, reformad...   
..     ...                                                ...   
993    0.0     Piso todo exterior con balcones en sant antoni   
994    0.0                                         Piso Avila   
995    0.0   Piso en Sagrada Família. Piso carrer de mallorca   
996    0.0  Apartamento en Poblenou. Apartamento con 3 hab...   
997    0.0  Piso Carrer de buenaventura muñoz. Piso con 4 ...   

                                                  desc  APARTMENT  DUPLEX  \
0    Piso en última planta a reformar en calle Tall...          0       0   
1    Ubicado en la zona del Camp de l’Arpa, cerca d...          0       0   
2    En pleno centro de Barcelona, justo al lado de...          0       0   
3    Vivienda espaciosa en Sant Antoni, cerca de Pl...          0       0   
4    En el corazón de Barcelona, en una hermosa fin...          0       0   
..                                                 ...        ...     ...   
993  Encantador piso alto todo exterior con 2 balco...          0       0   
994  Estupenda oportunidad en el Parc i La Llacuna ...          0       0   
995  ¡OPORTUNIDAD EN SAGRADA FAMILIA!\n\nPiso situa...          0       0   
996  Piso en venta, Barcelona, Poblenou, carrer del...          1       0   
997  Oportunidad Única Inversión Barcelona! Piso 10...          0       0   

     FLAT  GROUND_FLOOR  LOFT  PENTHOUSE  STUDIO  ...  \
0       1             0     0          0       0  ...   
1       1             0     0          0       0  ...   
2       1             0     0          0       0  ...   
3       1             0     0          0       0  ...   
4       1             0     0          0       0  ...   
..    ...           ...   ...        ...     ...  ...   
993     1             0     0          0       0  ...   
994     1             0     0          0       0  ...   
995     1             0     0          0       0  ...   
996     0             0     0          0       0  ...   
997     1             0     0          0       0  ...   

     loc_string_Barcelona - La Nova Esquerra de l´Eixample\nVer mapa  \
0                                                    0                 
1                                                    0                 
2                                                    0                 
3                                                    0                 
4                                                    0                 
..                                                 ...                 
993                                                  0                 
994                                                  0                 
995                                                  0                 
996                                                  0                 
997                                                  0                 

     loc_string_Barcelona - La Vila Olímpica del Poblenou  \
0                                                    0      
1                                                    0      
2                                                    0      
3                                                    0      
4                                                    0      
..                                                 ...      
993                                                  0      
994                                                  0      
995                                                  0      
996                                                  0      
997                                                  0      

     loc_string_

## SpaCy: second attempt

In [38]:
# def vectorize_text(text):
#     doc = nlp(text)
#     return doc.vector

In [39]:
# # df['desc_vector'] = df['processed_desc'].apply(vectorize_text)
# # df['title_vector'] = df['processed_title'].apply(vectorize_text)
# tfidf_vectorizer_desc = TfidfVectorizer(max_features=5000)  # Adjust max_features as needed for 'desc'
# tfidf_vectorizer_title = TfidfVectorizer(max_features=5000)  # Adjust max_features as needed for 'title'

# # Fit and transform the 'desc' and 'title' columns
# desc_tfidf = tfidf_vectorizer_desc.fit_transform(df2['desc'])
# title_tfidf = tfidf_vectorizer_title.fit_transform(df2['title'])

# # Convert the vectorized data to DataFrames
# desc_tfidf_df = pd.DataFrame(desc_tfidf.toarray(), columns=tfidf_vectorizer_desc.get_feature_names_out())
# title_tfidf_df = pd.DataFrame(title_tfidf.toarray(), columns=tfidf_vectorizer_title.get_feature_names_out())

# # Concatenate the vectorized DataFrames with the original DataFrame
# df2 = pd.concat([df2.drop(['desc', 'title'], axis=1), desc_tfidf_df.add_prefix('desc_'), title_tfidf_df.add_prefix('title_')], axis=1)


In [40]:
# Download Spanish stopwords
nltk.download('stopwords')
spanish_stopwords = stopwords.words('spanish')

# Function to preprocess text
def preprocess_text(text):
    text = text.lower()
    # Tokenize
    tokens = [word for word in text.split() if word not in spanish_stopwords]
    return ' '.join(tokens)

df['title_processed'] = df['title'].apply(preprocess_text)
df['desc_processed'] = df['desc'].apply(preprocess_text)

combined_text = df['title_processed'] + ' ' + df['desc_processed']

# Vectorize
vectorizer = CountVectorizer()
vectorizer.fit(combined_text)

title_vectors = vectorizer.transform(df['title_processed'])
desc_vectors = vectorizer.transform(df['desc_processed'])

# Vectors to dataframe
title_vectors_df = pd.DataFrame(title_vectors.toarray(), columns=vectorizer.get_feature_names_out())
desc_vectors_df = pd.DataFrame(desc_vectors.toarray(), columns=vectorizer.get_feature_names_out())

# Put the encoded vectors into the original dataframe
for column in title_vectors_df.columns:
    df[f'title_{column}'] = title_vectors_df[column]

for column in desc_vectors_df.columns:
    df[f'desc_{column}'] = desc_vectors_df[column]


string_columns = df.select_dtypes(include='object').columns
df = df.drop(columns=string_columns)

df2 = df
# df2 = df2.drop(['desc', 'title'], axis=1)

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/ouyangjiaxuan/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
/var/folders/xr/cvhhz_vs2jv7x1588g0qzl5m0000gn/T/ipykernel_84269/1959777643.py:35: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'title_{column}'] = title_vectors_df[column]
/var/folders/xr/cvhhz_vs2jv7x1588g0qzl5m0000gn/T/ipykernel_84269/1959777643.py:35: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'title_{column}'] = title_vectors_df[column]
/var/folders/xr/cvhhz_vs2jv7

In [41]:
df2.shape

(998, 15829)

In [42]:
df2['desc_últimos']

0      0
1      0
2      0
3      0
4      0
      ..
993    0
994    0
995    0
996    0
997    0
Name: desc_últimos, Length: 998, dtype: int64

In [43]:
desc_vectors_df.columns

Index(['00', '000', '000eur', '001661', '002203', '002266', '00238', '002569',
       '00h', '00hs',
       ...
       'último', 'últimos', 'única', 'únicamente', 'únicas', 'único', 'únicos',
       'útil', 'útiles', 'útils'],
      dtype='object', length=7896)

## Then we will start to split the encoded train and test dataset

In [44]:
train_df = df2[df2['price'] != 0.0]
test_df = df2[df2['price'] == 0.0]

In [45]:
train_df.columns

Index(['price', 'APARTMENT', 'DUPLEX', 'FLAT', 'GROUND_FLOOR', 'LOFT',
       'PENTHOUSE', 'STUDIO', 'square_m', 'hab',
       ...
       'desc_último', 'desc_últimos', 'desc_única', 'desc_únicamente',
       'desc_únicas', 'desc_único', 'desc_únicos', 'desc_útil', 'desc_útiles',
       'desc_útils'],
      dtype='object', length=15829)

In [46]:
train_df.shape, test_df.shape

((866, 15829), (132, 15829))

## Scaling

In [47]:
test_df.iloc[:, 1:]

APARTMENT  DUPLEX  FLAT  GROUND_FLOOR  LOFT  PENTHOUSE  STUDIO  square_m  \
866          0       0     1             0     0          0       0      87.0   
867          0       0     1             0     0          0       0      78.0   
868          0       0     1             0     0          0       0      65.0   
869          0       0     1             0     0          0       0      88.0   
870          0       0     1             0     0          0       0      82.0   
..         ...     ...   ...           ...   ...        ...     ...       ...   
993          0       0     1             0     0          0       0      89.0   
994          0       0     1             0     0          0       0      65.0   
995          0       0     1             0     0          0       0      75.0   
996          1       0     0             0     0          0       0      75.0   
997          0       0     1             0     0          0       0      80.0   

     hab  bano  ...  desc_último  desc_últimos  desc_única  desc_únicamente  \
866  4.0   1.0  ...            0             0           0                0   
867  4.0   1.0  ...            0             0           0                0   
868  1.0   1.0  ...            0             0           0                0   
869  3.0   1.0  ...            0             0           0                0   
870  2.0   1.0  ...            0             0           1                0   
..   ...   ...  ...          ...           ...         ...              ...   
993  3.0   1.0  ...            0             0           0                0   
994  3.0   1.0  ...            0             0           0                0   
995  4.0   1.0  ...            0             0           0                0   
996  3.0   2.0  ...            0             0           0                0   
997  4.0   2.0  ...            0             0           2                0   

     desc_únicas  desc_único  desc_únicos  desc_útil  desc_útiles  desc_útils  
866            0           0            0          0            0           0  
867            0           0            0          0            0           0  
868            0           0            0          0            0           0  
869            0           0            0          0            0           0  
870            0           0            0          0            1           0  
..           ...         ...          ...        ...          ...         ...  
993            0           0            0          0            0           0  
994            0           0            0          0            0           0  
995            0           0            0          0            0           0  
996            0           0            0          0            0           0  
997            0           0            0          0            0           0  

[132 rows x 15828 columns]

In [48]:
test_df

price  APARTMENT  DUPLEX  FLAT  GROUND_FLOOR  LOFT  PENTHOUSE  STUDIO  \
866    0.0          0       0     1             0     0          0       0   
867    0.0          0       0     1             0     0          0       0   
868    0.0          0       0     1             0     0          0       0   
869    0.0          0       0     1             0     0          0       0   
870    0.0          0       0     1             0     0          0       0   
..     ...        ...     ...   ...           ...   ...        ...     ...   
993    0.0          0       0     1             0     0          0       0   
994    0.0          0       0     1             0     0          0       0   
995    0.0          0       0     1             0     0          0       0   
996    0.0          1       0     0             0     0          0       0   
997    0.0          0       0     1             0     0          0       0   

     square_m  hab  ...  desc_último  desc_últimos  desc_única  \
866      87.0  4.0  ...            0             0           0   
867      78.0  4.0  ...            0             0           0   
868      65.0  1.0  ...            0             0           0   
869      88.0  3.0  ...            0             0           0   
870      82.0  2.0  ...            0             0           1   
..        ...  ...  ...          ...           ...         ...   
993      89.0  3.0  ...            0             0           0   
994      65.0  3.0  ...            0             0           0   
995      75.0  4.0  ...            0             0           0   
996      75.0  3.0  ...            0             0           0   
997      80.0  4.0  ...            0             0           2   

     desc_únicamente  desc_únicas  desc_único  desc_únicos  desc_útil  \
866                0            0           0            0          0   
867                0            0           0            0          0   
868                0            0           0            0          0   
869                0            0           0            0          0   
870                0            0           0            0          0   
..               ...          ...         ...          ...        ...   
993                0            0           0            0          0   
994                0            0           0            0          0   
995                0            0           0            0          0   
996                0            0           0            0          0   
997                0            0           0            0          0   

     desc_útiles  desc_útils  
866            0           0  
867            0           0  
868            0           0  
869            0           0  
870            1           0  
..           ...         ...  
993            0           0  
994            0           0  
995            0           0  
996            0           0  
997            0           0  

[132 rows x 15829 columns]

In [49]:
train_df.iloc[:, 1:]

APARTMENT  DUPLEX  FLAT  GROUND_FLOOR  LOFT  PENTHOUSE  STUDIO  square_m  \
0            0       0     1             0     0          0       0      85.0   
1            0       0     1             0     0          0       0      65.0   
2            0       0     1             0     0          0       0      77.0   
3            0       0     1             0     0          0       0      96.0   
4            0       0     1             0     0          0       0      84.0   
..         ...     ...   ...           ...   ...        ...     ...       ...   
861          0       0     1             0     0          0       0     115.0   
862          0       0     1             0     0          0       0      82.0   
863          0       0     1             0     0          0       0      79.0   
864          0       0     1             0     0          0       0      63.0   
865          0       0     1             0     0          0       0      80.0   

     hab  bano  ...  desc_último  desc_últimos  desc_única  desc_únicamente  \
0    2.0   1.0  ...            0             0           0                0   
1    2.0   1.0  ...            0             0           0                0   
2    2.0   1.0  ...            0             0           1                0   
3    3.0   2.0  ...            0             0           0                0   
4    2.0   1.0  ...            0             0           0                0   
..   ...   ...  ...          ...           ...         ...              ...   
861  3.0   1.0  ...            0             0           0                0   
862  3.0   1.0  ...            0             0           0                0   
863  4.0   2.0  ...            0             0           0                0   
864  1.0   1.0  ...            0             0           0                0   
865  2.0   1.0  ...            0             0           0                0   

     desc_únicas  desc_único  desc_únicos  desc_útil  desc_útiles  desc_útils  
0              0           0            0          0            0           0  
1              0           0            0          0            0           0  
2              0           0            0          0            0           0  
3              0           0            0          0            0           0  
4              0           0            0          0            0           0  
..           ...         ...          ...        ...          ...         ...  
861            0           0            0          0            0           0  
862            0           0            0          0            1           0  
863            0           0            0          0            0           0  
864            0           0            0          0            0           0  
865            0           0            0          0            0           0  

[866 rows x 15828 columns]

In [50]:
X = train_df.iloc[:, 1:].values 
y = train_df.iloc[:, 0].values
X_val = test_df.iloc[:, 1:].values

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1, random_state=5)

# scaler = StandardScaler()
# # X_train = scaler.fit_transform(X_train)
# # X_test = scaler.transform(X_test)
# # X_val = scaler.transform(X_val)
# scaler = StandardScaler()

# # Fit the scaler on the training data and transform it
# X_train = scaler.fit_transform(X_train)

# # Transform the validation and test data using the same scaler
# X_val = scaler.transform(X_val)
# X_test = scaler.transform(X_test)



In [51]:
test_df = test_df.drop('price', axis=1)

In [52]:
test_df

APARTMENT  DUPLEX  FLAT  GROUND_FLOOR  LOFT  PENTHOUSE  STUDIO  square_m  \
866          0       0     1             0     0          0       0      87.0   
867          0       0     1             0     0          0       0      78.0   
868          0       0     1             0     0          0       0      65.0   
869          0       0     1             0     0          0       0      88.0   
870          0       0     1             0     0          0       0      82.0   
..         ...     ...   ...           ...   ...        ...     ...       ...   
993          0       0     1             0     0          0       0      89.0   
994          0       0     1             0     0          0       0      65.0   
995          0       0     1             0     0          0       0      75.0   
996          1       0     0             0     0          0       0      75.0   
997          0       0     1             0     0          0       0      80.0   

     hab  bano  ...  desc_último  desc_últimos  desc_única  desc_únicamente  \
866  4.0   1.0  ...            0             0           0                0   
867  4.0   1.0  ...            0             0           0                0   
868  1.0   1.0  ...            0             0           0                0   
869  3.0   1.0  ...            0             0           0                0   
870  2.0   1.0  ...            0             0           1                0   
..   ...   ...  ...          ...           ...         ...              ...   
993  3.0   1.0  ...            0             0           0                0   
994  3.0   1.0  ...            0             0           0                0   
995  4.0   1.0  ...            0             0           0                0   
996  3.0   2.0  ...            0             0           0                0   
997  4.0   2.0  ...            0             0           2                0   

     desc_únicas  desc_único  desc_únicos  desc_útil  desc_útiles  desc_útils  
866            0           0            0          0            0           0  
867            0           0            0          0            0           0  
868            0           0            0          0            0           0  
869            0           0            0          0            0           0  
870            0           0            0          0            1           0  
..           ...         ...          ...        ...          ...         ...  
993            0           0            0          0            0           0  
994            0           0            0          0            0           0  
995            0           0            0          0            0           0  
996            0           0            0          0            0           0  
997            0           0            0          0            0           0  

[132 rows x 15828 columns]

In [53]:
X_train.shape

(779, 15828)

In [54]:
y_test.shape

(87,)

# Model 1: Random forest

In [55]:
rf_regressor = RandomForestRegressor(n_estimators=500, random_state=5)

rf_regressor.fit(X_train, y_train)

y_pred = rf_regressor.predict(X_test)

r2 = r2_score(y_test, y_pred)
mse = mean_squared_error(y_test, y_pred)

print(f'R-squared: {r2:.4f}')
print(f'Mean Squared Error: {mse:.4f}')

KeyboardInterrupt: 

In [57]:
scaler = StandardScaler()
X_train_new = scaler.fit_transform(X_train)

X_test_new = test_df.values

X_test_new_scaled = scaler.transform(X_test_new)

## Model 2: LASSO Regression

In [58]:

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

lasso = Lasso(alpha=0.1)

lasso.fit(X_train_scaled, y_train)

y_pred = lasso.predict(X_test_scaled)
y_pred_new = lasso.predict(X_test_new_scaled)

r2 = r2_score(y_test, y_pred)
mse = mean_squared_error(y_test, y_pred)

print(f'R-squared: {r2}')
print(f'Mean Squared Error: {mse}')

R-squared: 0.4973315343096605
Mean Squared Error: 2733.914594368731


In [59]:
X_test_scaled.shape

(87, 15828)

In [60]:
X_train.shape

(779, 15828)

## Model 3: Ridge Regression

In [61]:
ridge = Ridge(alpha=1.0)  # You can adjust the alpha value as needed
ridge.fit(X_train_scaled, y_train)

y_pred_ridge = ridge.predict(X_test_scaled)

r2_ridge = r2_score(y_test, y_pred_ridge)
mse_ridge = mean_squared_error(y_test, y_pred_ridge)

print(f'Ridge R-squared: {r2_ridge}')
print(f'Ridge Mean Squared Error: {mse_ridge}')

Ridge R-squared: 0.47072185146210777
Ridge Mean Squared Error: 2878.6394085432953


## Model 4: xgb boosting

In [62]:
# from sklearn.model_selection import GridSearchCV

# param_grid = {
#     'max_depth': [3, 4, 5],
#     'learning_rate': [0.01, 0.05, 0.1],
#     'n_estimators': [200, 600, 1000]
# }

# xgb_model = xgb.XGBRegressor(objective='reg:squarederror')
# grid_search = GridSearchCV(estimator=xgb_model, param_grid=param_grid, cv=5, scoring='neg_mean_squared_error', verbose=1)
# grid_search.fit(X_train, y_train)

# best_params = grid_search.best_params_
# print(f"Best parameters: {best_params}")

In [63]:
dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_test, label=y_test)

params = {
    'objective': 'reg:squarederror',  
    'max_depth': 5,                   
    'learning_rate': 0.1,             
    'n_estimators': 600           
}

num_rounds = 800
bst = xgb.train(params, dtrain, num_rounds)

y_pred_xgb = bst.predict(dtest)

r2_xgb = r2_score(y_test, y_pred_xgb)
mse_xgb = mean_squared_error(y_test, y_pred_xgb)

dval = xgb.DMatrix(X_val)
y_pred_val = bst.predict(dval)

print(f'XGBoost R-squared: {r2_xgb}')
print(f'XGBoost Mean Squared Error: {mse_xgb}')

/Users/ouyangjiaxuan/anaconda3/lib/python3.10/site-packages/xgboost/core.py:160: UserWarning: [20:06:11] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "n_estimators" } are not used.

  warnings.warn(smsg, UserWarning)


XGBoost R-squared: 0.6604298662224962
XGBoost Mean Squared Error: 1846.8549509488385


In [64]:
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.metrics import r2_score, mean_squared_error

model = GradientBoostingRegressor(loss='huber', alpha=0.9, n_estimators=200, learning_rate=0.1, max_depth=5)

model.fit(X_train, y_train)

y_pred = model.predict(X_test)

r2 = r2_score(y_test, y_pred)
mse = mean_squared_error(y_test, y_pred)

print(f'R-squared: {r2}')
print(f'Mean Squared Error: {mse}')

R-squared: 0.6777846039785509
Mean Squared Error: 1752.4659568678996


In [65]:
y_pred_val2 = model.predict(X_val)

In [66]:
y_pred_val2.shape

(132,)

## Output predicted value csv file

In [63]:
test_pickle_file_path = 'data/test_kaggle.pickle'

with open(test_pickle_file_path, 'rb') as file:
    test_data = pickle.load(file)
test_data = pd.DataFrame(test_data)

In [64]:
test_data['price'] = y_pred_val2
predictions = test_data[['id', 'price']]
predictions.to_csv('data/prediction_gb_2.csv', index=False)